In [20]:
import os
import pandas as pd
from datetime import datetime
from geopy.distance import geodesic
import numpy as np
from scipy.signal import medfilt
from openai import AzureOpenAI
from qdrant_client import QdrantClient
from qdrant_client.http.models import Distance, VectorParams
from qdrant_client.models import PointStruct
from haversine import haversine
import uuid
from geopy.geocoders import Nominatim # Openstreetmap as a source
import geopandas as gpd
from datetime import datetime

In [3]:
# Initialize the Azure OpenAI client
azure_openai = AzureOpenAI(
    azure_endpoint="https://intelligencia-openai-lab02.openai.azure.com/",
    api_key="049425cc99184a619ff068082279749f",
    api_version="2024-02-15-preview"
)

In [3]:
import os
import uuid
import numpy as np
import pandas as pd
import geopandas as gpd
from geopy.distance import geodesic
from geopy.geocoders import Nominatim
from scipy.signal import medfilt
from qdrant_client import QdrantClient
from qdrant_client.models import PointStruct, VectorParams, Distance

# Assuming azure_openai is configured for embedding generation
# from azure_openai import embeddings

# # Configure Qdrant Client
# qdrant_client = QdrantClient(host="localhost", port=6333)
# qdrant_collection_name = "trajectory_embeddings"

# # Create Qdrant collection if not exists
# qdrant_client.recreate_collection(
#     collection_name=qdrant_collection_name,
#     vectors_config=VectorParams(size=1536, distance=Distance.COSINE)
# )

# Function to compute bearing (unchanged)
def compute_bearing(lat1, lon1, lat2, lon2):
    dlon = np.radians(lon2 - lon1)
    lat1, lat2 = np.radians(lat1), np.radians(lat2)
    y = np.sin(dlon) * np.cos(lat2)
    x = np.cos(lat1) * np.sin(lat2) - np.sin(lat1) * np.cos(lat2) * np.cos(dlon)
    return np.degrees(np.arctan2(y, x)) % 360

# Semantic Enrichment (unchanged)
def get_location_name(lat, lon):
    geolocator = Nominatim(user_agent="geoenrichment")
    try:
        location = geolocator.reverse((lat, lon), exactly_one=True)
        return location.address
    except Exception as e:
        return "Unknown Location"

# Read .plt files (unchanged)
def read_plt(file_path):
    columns = ['lat', 'lon', 'zero', 'altitude', 'timestamp_days', 'date', 'time']
    df = pd.read_csv(file_path, skiprows=6, header=None, names=columns)
    df['datetime'] = pd.to_datetime(df['date'] + ' ' + df['time'])
    return df[['lat', 'lon', 'datetime']]

# Manual time difference calculation (unchanged)
def calculate_time_differences_manually(df, datetime_column='datetime', output_column='time_diff'):
    df[datetime_column] = pd.to_datetime(df[datetime_column])
    df = df.sort_values(datetime_column).drop_duplicates(subset=[datetime_column]).reset_index(drop=True)
    datetimes = df[datetime_column].tolist()
    time_diffs = [float('nan')]
    for i in range(1, len(datetimes)):
        delta = datetimes[i] - datetimes[i-1]
        time_diffs.append(delta.total_seconds())
    df[output_column] = time_diffs
    return df

# Check raw GPS data (unchanged)
def check_raw_gps_data(df):
    if not pd.api.types.is_datetime64_any_dtype(df['datetime']):
        df['datetime'] = pd.to_datetime(df['datetime'])
    else:
        print("Datetime column is already in datetime64 format; proceeding as-is.")
    
    df['lat_diff'] = df['lat'].diff().abs()
    df['lon_diff'] = df['lon'].diff().abs()
    # df = calculate_time_differences_manually(df)
    
    print("\nFirst 20 rows with differences:")
    print(df[['datetime', 'lat_diff', 'lon_diff', 'time_diff']].iloc[:20])
    print("\nTime Difference Statistics (seconds):")
    print(df['time_diff'].describe())
    
    print("\nPotential Latitude Outliers:")
    print(df[df['lat_diff'] > df['lat_diff'].mean() + 3 * df['lat_diff'].std()][['lat', 'lat_diff', 'datetime']])
    print("\nPotential Longitude Outliers:")
    print(df[df['lon_diff'] > df['lon_diff'].mean() + 3 * df['lon_diff'].std()][['lon', 'lon_diff', 'datetime']])
    print("\nPotential Time Outliers (time differences < 0.5 sec):")
    print(df[df['time_diff'] < 0.5][['datetime', 'time_diff']])

# Data cleaning function (unchanged, but can use speed cap if called)
def clean_trajectory(df):
    if len(df) < 10:
        print(f"Data discarded: insufficient rows ({len(df)} rows).")
        return pd.DataFrame()
    
    if 'time_diff' not in df.columns:
        df = calculate_time_differences_manually(df)
    
    df['next_lat'] = df['lat'].shift(-1)
    df['next_lon'] = df['lon'].shift(-1)
    df['distance'] = df.apply(
        lambda row: geodesic((row['lat'], row['lon']), (row['next_lat'], row['next_lon'])).meters
        if pd.notna(row['next_lat']) else np.nan,
        axis=1
    )
    
    df['speed'] = df['distance'] / df['time_diff']
    df['speed'] = medfilt(df['speed'], kernel_size=5)
    
    mean_speed = df['speed'].mean()
    if mean_speed > 15:
        print(f"Data discarded: mean speed too high ({mean_speed:.2f} m/s).")
        return pd.DataFrame()
    
    zero_speed_count = (df['speed'] == 0).sum()
    if zero_speed_count > len(df) * 0.5:
        print(f"Data discarded: more than 50% of rows have zero speed ({zero_speed_count} rows).")
        return pd.DataFrame()
    
    df['bearing'] = np.where(
        pd.notna(df['next_lat']),
        compute_bearing(df['lat'], df['lon'], df['next_lat'], df['next_lon']),
        np.nan
    )
    df['bearing_change'] = df['bearing'].diff().abs().fillna(0)
    
    print(f"Data retained: {len(df)} rows after cleaning.")
    return df

# Updated compute_enriched_metrics with speed cap and outlier filter
def compute_enriched_metrics(df):
    if 'time_diff' not in df.columns:
        df = calculate_time_differences_manually(df)
    
    # Compute step distances
    df['next_lat'] = df['lat'].shift(-1)
    df['next_lon'] = df['lon'].shift(-1)
    df = df.dropna(subset=['lat', 'lon', 'next_lat', 'next_lon'])
    df['step_distance'] = df.apply(
        lambda row: geodesic((row['lat'], row['lon']), (row['next_lat'], row['next_lon'])).meters,
        axis=1
    )
    total_distance = df['step_distance'].sum() / 1000  # km
    
    # Compute raw speed (m/s)
    df['speed'] = df['step_distance'] / df['time_diff']
    
    # Apply speed cap based on transport mode (if known, else default)
    if 'transport_mode' in df.columns and not df['transport_mode'].isna().all():
        mode = df['transport_mode'].mode()[0] if not df['transport_mode'].mode().empty else 'unknown'
    else:
        mode = 'unknown'
    
    speed_cap_mps = {
    'walk': 2.78,  # 10 km/h
    'bike': 6.94,  # 25 km/h
    'bus': 11.11,  # 40 km/h
    'car': 13.89,  # 50 km/h
    'taxi': 13.89,  # 50 km/h
    'unknown': 13.89  # Default to car cap
    }.get(mode.lower(), 6.94)  # Default to 25 km/h if mode not recognized
    
    accel_cap_mps2 = {
    'walk': 2.0,  # 2 m/s²
    'bike': 3.0,  # 3 m/s²
    'bus': 3.5,   # 3.5 m/s²
    'car': 4.0,   # 4 m/s²
    'taxi': 4.0,  # 4 m/s²
    'unknown': 4.0
    }.get(mode.lower(), 4.0)
    df['acceleration'] = df['acceleration'].clip(upper=accel_cap_mps2)
    
    df['speed'] = df['speed'].clip(upper=speed_cap_mps)
    
    # Outlier filter: Cap speeds exceeding mean + 3*std (pre-smoothing)
    speed_mean = df['speed'].mean()
    speed_std = df['speed'].std()
    speed_threshold = speed_mean + 3 * speed_std
    df['speed'] = df['speed'].clip(upper=min(speed_threshold, speed_cap_mps))
    
    # Smooth speeds
    df['speed'] = medfilt(df['speed'], kernel_size=5)
    df['speed_kmh'] = df['speed'] * 3.6  # Convert to km/h
    
    # Compute metrics
    max_speed = df['speed_kmh'].max()
    min_speed = df['speed_kmh'].min()
    speed_std = df['speed_kmh'].std()
    avg_speed = df['speed_kmh'].mean()
    
    # Compute acceleration (m/s²)
    df['acceleration'] = df['speed'].diff() / df['time_diff']
    df['acceleration'] = df['acceleration'].fillna(0)
    
    avg_acceleration = df['acceleration'].mean()
    max_acceleration = df['acceleration'].max()
    acceleration_std = df['acceleration'].std()
    
    # Turning metrics
    if 'bearing' not in df.columns or df['bearing'].isnull().all():
        df['bearing'] = df.apply(
            lambda row: compute_bearing(row['lat'], row['lon'], row['next_lat'], row['next_lon']),
            axis=1
        )
    df['bearing_change'] = df['bearing'].diff().abs()
    turn_threshold = 30
    num_turns = (df['bearing_change'] >= turn_threshold).sum()
    duration_minutes = df['time_diff'].sum() / 60
    turn_rate = num_turns / duration_minutes if duration_minutes > 0 else 0
    avg_turn_angle = df['bearing_change'].mean()
    turn_angle_std = df['bearing_change'].std()
    avg_bearing_change = avg_turn_angle
    
    metrics = {
        "total_distance": total_distance,
        "max_speed": max_speed,
        "min_speed": min_speed,
        "speed_std": speed_std,
        "avg_speed": avg_speed,
        "avg_acceleration": avg_acceleration,
        "max_acceleration": max_acceleration,
        "acceleration_std": acceleration_std,
        "num_turns": int(num_turns),
        "turn_rate": turn_rate,
        "avg_turn_angle": avg_turn_angle,
        "turn_angle_std": turn_angle_std,
        "avg_bearing_change": avg_bearing_change
    }
    return metrics

# Trip description (unchanged)
def generate_trip_description(df, metrics):
    if df.empty:
        return "No valid data for this trip.", "Unknown"

    start = df.iloc[0]
    end = df.iloc[-1]
    
    start_location = get_location_name(start['lat'], start['lon'])
    end_location = get_location_name(end['lat'], end['lon'])

    if 'transport_mode' in df.columns and not df['transport_mode'].isna().all():
        mode_series = df['transport_mode']
        mode_value = mode_series.mode()[0]
        mode_count = (mode_series == mode_value).sum()
        total_points = len(mode_series)
        threshold = 0.6
        if (mode_count / total_points) >= threshold:
            transport_mode = mode_value
        else:
            transport_mode = "Mixed"
    else:
        transport_mode = "Unknown"

    description = f"""
Trip Summary:
- Start: {start['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {start_location}
- End: {end['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {end_location}
- Duration: {(end['datetime'] - start['datetime'])}
- Distance: {metrics['total_distance']:.2f} km
- Average Speed: {metrics['avg_speed']:.2f} km/h
- Average Bearing Change: {metrics['avg_bearing_change']:.2f}°
- Max Speed: {metrics['max_speed']:.2f} km/h
- Min Speed: {metrics['min_speed']:.2f} km/h
- Speed Variability: {metrics['speed_std']:.2f} km/h
- Average Acceleration: {metrics['avg_acceleration']:.2f} m/s²
- Max Acceleration: {metrics['max_acceleration']:.2f} m/s²
- Number of Turns: {metrics['num_turns']}
- Turn Rate: {metrics['turn_rate']:.2f} turns/min
- Average Turn Angle: {metrics['avg_turn_angle']:.2f}°
- Turn Angle Variability: {metrics['turn_angle_std']:.2f}°
- Transport Mode: {transport_mode}
    """
    
    with open("trip_summaries.txt", "a", encoding="utf-8") as f:
        f.write(description + "\n\n")

    return description, transport_mode

# Embedding generation (unchanged)
def generate_embedding(text):
    response = azure_openai.embeddings.create(
        input=text,
        model="text-embedding-ada-002"
    )
    return np.array(response.data[0].embedding)

# Main pipeline
def process_trajectory_folder(folder_path):
    trip_summaries = []
    
    for root, _, files in os.walk(folder_path):
        for file in files:
            if file.endswith('.geojson'):
                file_path = os.path.join(root, file)
                print(f"Processing {file_path}...")

                gdf = gpd.read_file(file_path)
                if gdf.empty:
                    print(f"Skipping {file_path}: No valid data.")
                    continue

                df = gdf.copy()
                # print("Raw datetime values:")
                # print(df['datetime'].head(10))

                # Calculate time differences here
                df = calculate_time_differences_manually(df)

                # check_raw_gps_data(df)
                if df.empty:
                    print(f"Skipping {file_path}: No valid data after checking.")
                    continue

                metrics = compute_enriched_metrics(df)
                trip_description, transport_mode = generate_trip_description(df, metrics)
                if trip_description.strip() == "No valid data for this trip.":
                    print(f"Skipping {file_path}: Trip description indicates no valid data.")
                    continue

                # start = df.iloc[0]
                # end = df.iloc[-1]
                # start_location = get_location_name(start['lat'], start['lon'])
                # end_location = get_location_name(end['lat'], end['lon'])
                # embedding = generate_embedding(trip_description)

                # point = PointStruct(
                #     id=str(uuid.uuid4()),
                #     vector=embedding.tolist(),
                #     payload={
                #         "description": trip_description,
                #         "start_datetime": start['datetime'].strftime('%Y-%m-%d %H:%M:%S'),
                #         "end_datetime": end['datetime'].strftime('%Y-%m-%d %H:%M:%S'),
                #         "duration": (end['datetime'] - start['datetime']).total_seconds(),
                #         "distance_km": metrics['total_distance'],
                #         "average_speed_kmh": metrics['avg_speed'],
                #         "average_bearing_change": metrics['avg_bearing_change'],
                #         "start_location": start_location,
                #         "end_location": end_location,
                #         "transport_mode": transport_mode,
                #         "max_speed": metrics['max_speed'],
                #         "min_speed": metrics['min_speed'],
                #         "speed_std": metrics['speed_std'],
                #         "avg_acceleration": metrics['avg_acceleration'],
                #         "max_acceleration": metrics['max_acceleration'],
                #         "acceleration_std": metrics['acceleration_std'],
                #         "num_turns": metrics['num_turns'],
                #         "turn_rate": metrics['turn_rate'],
                #         "avg_turn_angle": metrics['avg_turn_angle'],
                #         "turn_angle_std": metrics['turn_angle_std'],
                #         "file_name": file
                #     }
                # )

                # qdrant_client.upsert(
                #     collection_name=qdrant_collection_name,
                #     points=[point]
                # )
                trip_summaries.append(trip_description)

    print("Processing complete. Trip summaries and embeddings stored in Qdrant.")

# # Query Qdrant (unchanged)
# def query_qdrant(query_text, top_k=5):
#     query_embedding = generate_embedding(query_text)
#     search_result = qdrant_client.search(
#         collection_name=qdrant_collection_name,
#         query_vector=query_embedding.tolist(),
#         limit=top_k
#     )
    
#     print("Top matches:")
#     for i, result in enumerate(search_result):
#         print(f"Match {i+1}:")
#         print(result.payload['description'])
#         print("-" * 40)

# Run the pipeline
# process_trajectory_folder('./Filtered_Trajectories')

In [8]:
# Define the folder where your cleaned subtrajectory files are stored.
# (For instance, if you used the "Sub_Trajectories_Cleaned_LLM" folder.)
subtraj_folder = "./Sub_Trajectories_Cleaned"
trip_summary_output_file = "sub_trip_summaries.txt"

# (Optional) Clear the output file before appending new summaries.
with open(trip_summary_output_file, "w", encoding="utf-8") as f:
    f.write("")

# Iterate over each subtrajectory GeoJSON file.
for root, dirs, files in os.walk(subtraj_folder):
    for file in files:
        if file.endswith(".geojson"):
            file_path = os.path.join(root, file)
            print(f"Processing subtrajectory file: {file_path}")
            try:
                # Read the subtrajectory as a GeoDataFrame.
                gdf = gpd.read_file(file_path)
                if gdf.empty:
                    print(f"Skipping {file_path}: Empty file.")
                    continue

                # Ensure the DataFrame has a proper datetime column.
                if "datetime" not in gdf.columns:
                    if "date" in gdf.columns and "time" in gdf.columns:
                        gdf["datetime"] = pd.to_datetime(gdf["date"] + " " + gdf["time"], format="%Y-%m-%d %H:%M:%S")
                
                # Calculate time differences (if not already done).
                gdf = calculate_time_differences_manually(gdf)

                # If there are not enough points, skip.
                if len(gdf) < 2:
                    print(f"Skipping {file_path}: Not enough points for a trip summary.")
                    continue

                # Compute enriched metrics from the subtrajectory.
                metrics = compute_enriched_metrics(gdf)

                # Generate a trip summary using your pre-defined function.
                # The function generate_trip_description returns (description, transport_mode).
                trip_summary, transport_mode = generate_trip_description(gdf, metrics)
                
                # Print the trip summary to the console.
                # print(trip_summary)
                
                # The generate_trip_description function already appends the summary to "trip_summaries.txt"
                # If you want to  ensure it's saved here too, you could also append it manually:
                with open(trip_summary_output_file, "a", encoding="utf-8") as f:
                    f.write(trip_summary + "\n\n")
            
            except Exception as e:
                print(f"Error processing {file_path}: {e}")

print("Trip summary generation complete.")

Skipping field time: unsupported OGR type: 10


Processing subtrajectory file: ./Sub_Trajectories_Cleaned/20110929104547/walk_cleaned.geojson


/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
Skipping field time: unsupported OGR type: 10


Processing subtrajectory file: ./Sub_Trajectories_Cleaned/20081101040025/train_cleaned.geojson


/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
Skipping field time: unsupported OGR type: 10


...

Processing subtrajectory file: ./Sub_Trajectories_Cleaned/20081114075354/bike_cleaned.geojson


/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
Skipping field time: unsupported OGR type: 10


Processing subtrajectory file: ./Sub_Trajectories_Cleaned/20081114075354/car_cleaned.geojson


/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/mac/.pyenv/versions/3.11.5/lib/python3.11/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


Trip summary generation complete.


In [ ]:
# # Configure Qdrant Client

# qdrant_client = QdrantClient(host="localhost", port=6333)
# qdrant_collection_name = "trajectory_embeddings"

# # Create Qdrant collection if not exists
# qdrant_client.recreate_collection(
#     collection_name=qdrant_collection_name,
#     vectors_config=VectorParams(size=1536, distance=Distance.COSINE)  # 1536 is the dimension for text-embedding-ada-002
# )

# # Function to compute bearing (direction in degrees)
# def compute_bearing(lat1, lon1, lat2, lon2):
#     dlon = np.radians(lon2 - lon1)
#     lat1, lat2 = np.radians(lat1), np.radians(lat2)
#     y = np.sin(dlon) * np.cos(lat2)
#     x = np.cos(lat1) * np.sin(lat2) - np.sin(lat1) * np.cos(lat2) * np.cos(dlon)
#     return np.degrees(np.arctan2(y, x)) % 360

# # Semantic Enrichment - Convert GPS coordinates to human-readable locations
# def get_location_name(lat, lon):
#     geolocator = Nominatim(user_agent="geoenrichment")
#     try:
#         location = geolocator.reverse((lat, lon), exactly_one=True)
#         return location.address
#     except Exception as e:
#         return "Unknown Location"

# # Function to read and parse GeoLife trajectory .plt files
# def read_plt(file_path):
#     columns = ['lat', 'lon', 'zero', 'altitude', 'timestamp_days', 'date', 'time']
#     df = pd.read_csv(file_path, skiprows=6, header=None, names=columns)
#     df['datetime'] = pd.to_datetime(df['date'] + ' ' + df['time'])
#     return df[['lat', 'lon', 'datetime']]

# # Data cleaning function using median filter
# def clean_trajectory(df):
#     if len(df) < 10:
#         print(f"Data discarded: insufficient rows ({len(df)} rows).")
#         return pd.DataFrame()  # Discard segments with insufficient data
    
#     # Simplified speed calculation
#     df['speed'] = df['lat'].diff()**2 + df['lon'].diff()**2
#     df['speed'] = np.sqrt(df['speed']) * 111320  # Convert to meters (approximation)
    
#     # Apply a median filter to smooth speed values
#     df['speed'] = medfilt(df['speed'], kernel_size=5)
    
#     # Remove noisy segments based on mean speed threshold
#     mean_speed = df['speed'].mean()
#     if mean_speed > 15:  # Threshold: 15 m/s (54 km/h)
#         print(f"Data discarded: mean speed too high ({mean_speed:.2f} m/s).")
#         return pd.DataFrame()  # Remove high-speed noisy segments
    
#     # Remove segments with zero speed
#     zero_speed_count = (df['speed'] == 0).sum()
#     if zero_speed_count > len(df) * 0.5:
#         print(f"Data discarded: more than 50% of rows have zero speed ({zero_speed_count} rows).")
#         return pd.DataFrame()
    
#     # Compute the next lat/lon using shift()
#     df['next_lat'] = df['lat'].shift(-1)
#     df['next_lon'] = df['lon'].shift(-1)

#     # Compute bearing using a vectorized approach
#     df['bearing'] = np.where(
#         pd.notna(df['next_lat']),
#         compute_bearing(df['lat'], df['lon'], df['next_lat'], df['next_lon']),
#         np.nan
#     )
    
#     # Compute the absolute change in bearing
#     df['bearing_change'] = df['bearing'].diff().abs().fillna(0)
    
#     print(f"Data retained: {len(df)} rows after cleaning.")
#     return df


# # Function to create a descriptive text for each trip
# def generate_trip_description(df, metrics):
#     if df.empty:
#         return "No valid data for this trip.", "Unknown"

#     start = df.iloc[0]
#     end = df.iloc[-1]
    
#     start_location = get_location_name(start['lat'], start['lon'])
#     end_location = get_location_name(end['lat'], end['lon'])

#     # Determine transport mode (you can use your own logic here)
#     if 'transport_mode' in df.columns and not df['transport_mode'].isna().all():
#         mode_series = df['transport_mode']
#         mode_value = mode_series.mode()[0]
#         mode_count = (mode_series == mode_value).sum()
#         total_points = len(mode_series)
#         threshold = 0.6  # 60% threshold for a clear dominant mode
#         if (mode_count / total_points) >= threshold:
#             transport_mode = mode_value
#         else:
#             transport_mode = "Mixed"
#     else:
#         transport_mode = "Unknown"

#     # Build the description text including extra enriched features.
#     description = f"""
# Trip Summary:
# - Start: {start['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {start_location}
# - End: {end['datetime'].strftime('%Y-%m-%d %H:%M:%S')} at {end_location}
# - Duration: {(end['datetime'] - start['datetime'])}
# - Distance: {metrics['total_distance']:.2f} km
# - Average Speed: {metrics['avg_speed']:.2f} km/h
# - Average Bearing Change: {metrics['avg_bearing_change']:.2f}°
# - Max Speed: {metrics['max_speed']:.2f} km/h
# - Min Speed: {metrics['min_speed']:.2f} km/h
# - Speed Variability: {metrics['speed_std']:.2f} km/h
# - Average Acceleration: {metrics['avg_acceleration']:.2f} m/s²
# - Max Acceleration: {metrics['max_acceleration']:.2f} m/s²
# - Number of Turns: {metrics['num_turns']}
# - Turn Rate: {metrics['turn_rate']:.2f} turns/min
# - Average Turn Angle: {metrics['avg_turn_angle']:.2f}°
# - Turn Angle Variability: {metrics['turn_angle_std']:.2f}°
# - Transport Mode: {transport_mode}
#     """
    
#     # Optionally, append the description to a file.
#     with open("trip_summaries.txt", "a", encoding="utf-8") as f:
#         f.write(description + "\n\n")

#     return description, transport_mode


# # Function to generate embeddings using Azure OpenAI API
# def generate_embedding(text):
#     response = azure_openai.embeddings.create(
#         input=text,
#         model="text-embedding-ada-002"
#     )
#     return np.array(response.data[0].embedding)

# # function to compute the enriched metrics from a trajectory DataFrame.
# def compute_enriched_metrics(df):
#     # Compute total distance (km) using step distances with geodesic distances.
#     df['next_lat'] = df['lat'].shift(-1)
#     df['next_lon'] = df['lon'].shift(-1)
#     df = df[(df['lat'].between(-90, 90)) & (df['lon'].between(-180, 180))]
#     df = df[(df['next_lat'].between(-90, 90)) & (df['next_lon'].between(-180, 180))]
#     df = df.dropna(subset=['lat', 'lon', 'next_lat', 'next_lon'])
#     df['step_distance'] = df.apply(
#         lambda row: geodesic((row['lat'], row['lon']), (row['next_lat'], row['next_lon'])).meters,
#         axis=1
#     )
#     total_distance = df['step_distance'].sum() / 1000  # Convert to km

#     # Compute speed if not already present.
#     if 'speed' not in df.columns:
#         df['speed'] = np.sqrt((df['lat'].diff())**2 + (df['lon'].diff())**2) * 111320
#         df['speed'] = medfilt(df['speed'], kernel_size=5)
#         df['speed'] = df['speed'] * 3.6  # Convert to km/h

#     max_speed = df['speed'].max()
#     min_speed = df['speed'].min()
#     speed_std = df['speed'].std()
#     avg_speed = df['speed'].mean()

#     # Ensure datetime is in proper format and sort the DataFrame.
#     if not pd.api.types.is_datetime64_any_dtype(df['datetime']):
#         df['datetime'] = pd.to_datetime(df['datetime'])
#     df = df.sort_values('datetime').reset_index()

#     # --- Window-Based Acceleration Computation ---
#     # Convert speed from km/h to m/s.
#     df['speed_mps'] = df['speed'] / 3.6
#     # Convert datetime to seconds relative to the start of the trip.
#     df['time_seconds'] = (df['datetime'] - df['datetime'].iloc[0]).dt.total_seconds()

#     n = len(df)
#     window = 1  # Using one point on each side for the central difference.
#     accelerations = []
#     speeds = df['speed_mps'].to_numpy()
#     times = df['time_seconds'].to_numpy()

#     for i in range(n):
#         # For the first and last 'window' points, central difference is not available.
#         if i < window or i > n - window - 1:
#             accelerations.append(np.nan)
#         else:
#             dt = times[i + window] - times[i - window]
#             if dt > 0:
#                 a = (speeds[i + window] - speeds[i - window]) / dt
#             else:
#                 a = np.nan
#             accelerations.append(a)

#     df['acceleration'] = accelerations
#     # Optionally, fill boundary values.
#     df['acceleration'] = df['acceleration'].fillna(0)

#     avg_acceleration = df['acceleration'].mean()
#     max_acceleration = df['acceleration'].max()
#     acceleration_std = df['acceleration'].std()
#     # --- End Acceleration Computation ---

#     # Compute turning metrics.
#     if 'bearing' not in df.columns or df['bearing'].isnull().all():
#         df['bearing'] = df.apply(
#             lambda row: compute_bearing(row['lat'], row['lon'], row['next_lat'], row['next_lon'])
#             if pd.notna(row['next_lat']) else None, axis=1
#         )
#     df['bearing_change'] = df['bearing'].diff().abs()
#     turn_threshold = 30  # degrees threshold for a significant turn.
#     num_turns = (df['bearing_change'] >= turn_threshold).sum()
#     duration_minutes = (df.iloc[-1]['datetime'] - df.iloc[0]['datetime']).total_seconds() / 60
#     turn_rate = num_turns / duration_minutes if duration_minutes > 0 else None
#     avg_turn_angle = df['bearing_change'].mean()
#     turn_angle_std = df['bearing_change'].std()
#     avg_bearing_change = avg_turn_angle  # alias

#     metrics = {
#         "total_distance": total_distance,
#         "max_speed": max_speed,
#         "min_speed": min_speed,
#         "speed_std": speed_std,
#         "avg_speed": avg_speed,
#         "avg_acceleration": avg_acceleration,
#         "max_acceleration": max_acceleration,
#         "acceleration_std": acceleration_std,
#         "num_turns": int(num_turns),
#         "turn_rate": turn_rate,
#         "avg_turn_angle": avg_turn_angle,
#         "turn_angle_std": turn_angle_std,
#         "avg_bearing_change": avg_bearing_change
#     }
    
#     return metrics


# def calculate_time_differences_manually(df, datetime_column='datetime', output_column='time_diff'):
#     df[datetime_column] = pd.to_datetime(df[datetime_column])
#     df = df.sort_values(datetime_column).drop_duplicates(subset=[datetime_column]).reset_index(drop=True)
#     datetimes = df[datetime_column].tolist()
#     time_diffs = [float('nan')]
#     for i in range(1, len(datetimes)):
#         delta = datetimes[i] - datetimes[i-1]
#         time_diffs.append(delta.total_seconds())
#     df[output_column] = time_diffs
#     return df

# def check_raw_gps_data(df):
#     if not pd.api.types.is_datetime64_any_dtype(df['datetime']):
#         df['datetime'] = pd.to_datetime(df['datetime'])  # Flexible parsing if not already datetime64
#     else:
#         print("Datetime column is already in datetime64 format; proceeding as-is.")

#     # Compute differences between consecutive points.
#     df['lat_diff'] = df['lat'].diff().abs()
#     df['lon_diff'] = df['lon'].diff().abs()
#     # df['time_diff'] = df['datetime'].diff().dt.total_seconds()
#     df = calculate_time_differences_manually(df)
#     print("\nFirst 20 rows with differences:")
#     print(df[['datetime', 'lat_diff', 'lon_diff', 'time_diff']].iloc[:20])
#     print("\nTime Difference Statistics (seconds):")
#     print(df['time_diff'].describe())

#     print("After sorting and deduplication, DataFrame length:", len(df))
#     # Print first 20 rows to verify
#     print("\nFirst 20 rows with differences:")
#     print(df[['datetime', 'lat_diff', 'lon_diff', 'time_diff']].iloc[:20])
    
#     print("Latitude Difference Statistics:")
#     print(df['lat_diff'].describe())
#     print("\nLongitude Difference Statistics:")
#     print(df['lon_diff'].describe())
#     print("\nTime Difference Statistics (seconds):")
#     print(df['time_diff'].describe())
    
#     # Identify potential outliers:
#     lat_threshold = df['lat_diff'].mean() + 3 * df['lat_diff'].std()
#     lon_threshold = df['lon_diff'].mean() + 3 * df['lon_diff'].std()
#     lat_outliers = df[df['lat_diff'] > lat_threshold]
#     lon_outliers = df[df['lon_diff'] > lon_threshold]
#     time_outliers = df[df['time_diff'] < 0.5]
    
#     print("\nPotential Latitude Outliers:")
#     print(lat_outliers[['lat', 'lat_diff', 'datetime']])
#     print("\nPotential Longitude Outliers:")
#     print(lon_outliers[['lon', 'lon_diff', 'datetime']])
#     print("\nPotential Time Outliers (time differences < 0.5 sec):")
#     print(time_outliers[['datetime', 'time_diff']])
    
#     return df

# # Main pipeline to process all .plt files and store embeddings in Qdrant
# def process_trajectory_folder(folder_path):
#     trip_summaries = []
    
#     for root, _, files in os.walk(folder_path):
#         for file in files:
#             if file.endswith('.geojson'):  # Using cleaned trajectories
#                 file_path = os.path.join(root, file)
#                 print(f"Processing {file_path}...")

#                 # Read GeoJSON into a GeoDataFrame.
#                 gdf = gpd.read_file(file_path)
#                 if gdf.empty:
#                     print(f"Skipping {file_path}: No valid data.")
#                     continue

#                 df = gdf.copy()
#                 print("Raw datetime values:")
#                 print(df['datetime'].head(10))  # Print first 10 raw values
#                 # Example usage:
#                 df_checked = check_raw_gps_data(df)

#                 # Compute the enriched metrics first.
#                 metrics = compute_enriched_metrics(df)

#                 # Now generate the trip description using both the DataFrame and the computed metrics.
#                 trip_description, transport_mode = generate_trip_description(df, metrics)
#                 if trip_description.strip() == "No valid data for this trip.":
#                     print(f"Skipping {file_path}: Trip description indicates no valid data.")
#                     continue

#                 # Extract basic metadata.
#                 start = df.iloc[0]
#                 end = df.iloc[-1]

#                 # Enrich location info.
#                 start_location = get_location_name(start['lat'], start['lon'])
#                 end_location = get_location_name(end['lat'], end['lon'])

#                 # Generate embedding for the trip description.
#                 embedding = generate_embedding(trip_description)

#                 # Build the metadata payload including enriched features.
#                 point = PointStruct(
#                     id=str(uuid.uuid4()),
#                     vector=embedding.tolist(),
#                     payload={
#                         "description": trip_description,
#                         "start_datetime": start['datetime'].strftime('%Y-%m-%d %H:%M:%S'),
#                         "end_datetime": end['datetime'].strftime('%Y-%m-%d %H:%M:%S'),
#                         "duration": (end['datetime'] - start['datetime']).total_seconds(),
#                         "distance_km": metrics['total_distance'],
#                         "average_speed_kmh": metrics['avg_speed'],
#                         "average_bearing_change": metrics['avg_bearing_change'],
#                         "start_location": start_location,
#                         "end_location": end_location,
#                         "transport_mode": transport_mode,
#                         "max_speed": metrics['max_speed'],
#                         "min_speed": metrics['min_speed'],
#                         "speed_std": metrics['speed_std'],
#                         "avg_acceleration": metrics['avg_acceleration'],
#                         "max_acceleration": metrics['max_acceleration'],
#                         "acceleration_std": metrics['acceleration_std'],
#                         "num_turns": metrics['num_turns'],
#                         "turn_rate": metrics['turn_rate'],
#                         "avg_turn_angle": metrics['avg_turn_angle'],
#                         "turn_angle_std": metrics['turn_angle_std'],
#                         "file_name": file
#                     }
#                 )

#                 # Upsert the point into Qdrant.
#                 qdrant_client.upsert(
#                     collection_name=qdrant_collection_name,
#                     points=[point]
#                 )

#                 trip_summaries.append(trip_description)

#     print("Processing complete. Trip summaries and embeddings stored in Qdrant.")

# # Function to query Qdrant for similar trips
# def query_qdrant(query_text, top_k=5):
#     query_embedding = generate_embedding(query_text)
#     search_result = qdrant_client.search(
#         collection_name=qdrant_collection_name,
#         query_vector=query_embedding.tolist(),
#         limit=top_k  # Changed from top to limit
#     )
    
#     print("Top matches:")
#     for i, result in enumerate(search_result):
#         print(f"Match {i+1}:")
#         print(result.payload['description'])
#         print("-" * 40)


# # Example usage
# # Replace 'path_to_your_trajectory_folder' with the actual folder containing the .plt files
# process_trajectory_folder('./Filtered_Trajectories')

/var/folders/sl/r3dyv7l910q28kfxmr4rf6qr0000gn/T/ipykernel_80041/1776365454.py:7: DeprecationWarning: `recreate_collection` method is deprecated and will be removed in the future. Use `collection_exists` to check collection existence and `create_collection` instead.
  qdrant_client.recreate_collection(
Skipping field time: unsupported OGR type: 10


Processing ./Filtered_Trajectories/20080706052159_trajectory_321.geojson...
Raw datetime values:
0   2008-07-06 09:00:01
1   2008-07-06 09:00:02
2   2008-07-06 09:00:03
3   2008-07-06 09:00:04
4   2008-07-06 09:00:05
5   2008-07-06 09:00:06
6   2008-07-06 09:00:07
7   2008-07-06 09:00:08
8   2008-07-06 09:00:09
9   2008-07-06 09:00:10
Name: datetime, dtype: datetime64[ms]
Datetime column is already in datetime64 format; proceeding as-is.

First 20 rows with differences:
              datetime      lat_diff      lon_diff  time_diff
0  2008-07-06 09:00:01           NaN           NaN        NaN
1  2008-07-06 09:00:02  6.400000e-05  4.860000e-04        1.0
2  2008-07-06 09:00:03  0.000000e+00  1.940000e-04        1.0
3  2008-07-06 09:00:04  1.000000e-06  5.900000e-05        1.0
4  2008-07-06 09:00:05  6.400000e-05  4.200000e-05        1.0
5  2008-07-06 09:00:06  2.000000e-06  3.300000e-05        1.0
6  2008-07-06 09:00:07  1.000000e-06  2.400000e-05        1.0
7  2008-07-06 09:00:08  1.700

Skipping field time: unsupported OGR type: 10


Processing ./Filtered_Trajectories/20111207032835_trajectory_633.geojson...
Raw datetime values:
0   2011-12-07 03:28:35
1   2011-12-07 03:28:40
2   2011-12-07 03:28:45
3   2011-12-07 03:28:50
4   2011-12-07 03:28:55
5   2011-12-07 03:28:58
6   2011-12-07 03:29:00
7   2011-12-07 03:29:05
8   2011-12-07 03:29:10
9   2011-12-07 03:29:15
Name: datetime, dtype: datetime64[ms]
Datetime column is already in datetime64 format; proceeding as-is.

First 20 rows with differences:
              datetime  lat_diff  lon_diff  time_diff
0  2011-12-07 03:28:35       NaN       NaN        NaN
1  2011-12-07 03:28:40  0.000045  0.000230        5.0
2  2011-12-07 03:28:45  0.000108  0.000060        5.0
3  2011-12-07 03:28:50  0.000048  0.000103        5.0
4  2011-12-07 03:28:55  0.000018  0.000015        5.0
5  2011-12-07 03:28:58  0.000000  0.000000        3.0
6  2011-12-07 03:29:00  0.000007  0.000008        2.0
7  2011-12-07 03:29:05  0.000030  0.000007        5.0
8  2011-12-07 03:29:10  0.000008  0.000

Skipping field time: unsupported OGR type: 10


...

Skipping field time: unsupported OGR type: 10


Processing ./Filtered_Trajectories/20071002021612_trajectory_22.geojson...
Raw datetime values:
0   2007-10-02 08:07:23
1   2007-10-02 08:09:12
2   2007-10-02 08:09:24
3   2007-10-02 08:09:50
4   2007-10-02 08:10:07
5   2007-10-02 08:10:31
6   2007-10-02 08:10:50
7   2007-10-02 08:11:01
8   2007-10-02 08:11:07
9   2007-10-02 08:11:22
Name: datetime, dtype: datetime64[ms]
Datetime column is already in datetime64 format; proceeding as-is.

First 20 rows with differences:
              datetime  lat_diff  lon_diff  time_diff
0  2007-10-02 08:07:23       NaN       NaN        NaN
1  2007-10-02 08:09:12  0.004067  0.003450      109.0
2  2007-10-02 08:09:24  0.000133  0.000050       12.0
3  2007-10-02 08:09:50  0.000183  0.000033       26.0
4  2007-10-02 08:10:07  0.000733  0.000067       17.0
5  2007-10-02 08:10:31  0.001750  0.000200       24.0
6  2007-10-02 08:10:50  0.000267  0.000033       19.0
7  2007-10-02 08:11:01  0.000333  0.000033       11.0
8  2007-10-02 08:11:07  0.000217  0.0000

Skipping field time: unsupported OGR type: 10


Processing ./Filtered_Trajectories/20071005052724_trajectory_36.geojson...
Raw datetime values:
0   2007-10-05 09:33:14
1   2007-10-05 09:33:17
Name: datetime, dtype: datetime64[ms]
Datetime column is already in datetime64 format; proceeding as-is.

First 20 rows with differences:
             datetime  lat_diff  lon_diff  time_diff
0 2007-10-05 09:33:14       NaN       NaN        NaN
1 2007-10-05 09:33:17  0.000983  0.000167        3.0

Time Difference Statistics (seconds):
count    1.0
mean     3.0
std      NaN
min      3.0
25%      3.0
50%      3.0
75%      3.0
max      3.0
Name: time_diff, dtype: float64
After sorting and deduplication, DataFrame length: 2

First 20 rows with differences:
             datetime  lat_diff  lon_diff  time_diff
0 2007-10-05 09:33:14       NaN       NaN        NaN
1 2007-10-05 09:33:17  0.000983  0.000167        3.0
Latitude Difference Statistics:
count    1.000000
mean     0.000983
std           NaN
min      0.000983
25%      0.000983
50%      0.000983

TypeError: unsupported format string passed to NoneType.__format__

In [62]:
query_qdrant("Describe a walking trip with 2 km distance and 15 minutes duration.")

Top matches:
Match 1:

    Trip Summary:
    - Start: 2009-05-24 21:54:55 at 30, 双清路, 东升镇, 海淀区, 北京市, 100084, 中国
    - End: 2009-05-24 22:16:00 at 清华园街道, 西洼村, 海淀区, 北京市, 100084, 中国
    - Duration: 0 days 00:21:05
    - Distance: 2.25 km
    - Average Speed: 37.07 km/h
    - Average Bearing Change: 80.35 degrees
    
----------------------------------------
Match 2:

    Trip Summary:
    - Start: 2009-05-14 01:54:25 at 篮球馆, 百年银杏林, 清华园街道, 西洼村, 海淀区, 北京市, 100084, 中国
    - End: 2009-05-14 10:32:03 at 软件学院, 清华路, 清华园街道, 八家村总支委员会, 海淀区, 北京市, 100084, 中国
    - Duration: 0 days 08:37:38
    - Distance: 8.08 km
    - Average Speed: 42.77 km/h
    - Average Bearing Change: 75.27 degrees
    
----------------------------------------
Match 3:

    Trip Summary:
    - Start: 2009-04-30 03:23:32 at 清华大学西北小区, 清华园街道, 西洼村, 海淀区, 北京市, 100084, 中国
    - End: 2009-04-30 12:04:40 at 清华大学西北小区, 清华园街道, 西洼村, 海淀区, 北京市, 100084, 中国
    - Duration: 0 days 08:41:08
    - Distance: 31.17 km
    - Average Speed: 30.58 km/h


In [172]:
class SpatioAIQueryAssistant:
    def __init__(self, max_history=10):
        self.messages = [
          {
            "role": "system",
            "content": (
                "You are a specialized AI assistant for analyzing and predicting the mode of transportation based on GPS trajectory data. "
                "Your primary task is to classify the transportation mode (e.g., Walk, Bike, Bus, Car & Taxi, Train, Airplane, Other) by using trajectory features such as speed, acceleration, bearing rate, and bearing rate change. "
                "Additionally, use start and end locations when available to provide extra context for predicting the likely transportation mode.\n\n"
                
                "Consider the following patterns when deducing the mode of transportation:\n"
                "- Walk: Low speed (below 5 km/h) and high bearing rate change.\n"
                "- Bike: Medium speed (5–20 km/h) and moderate bearing rate change.\n"
                "- Bus: Variable speed (10–40 km/h), frequent stops, and a mix of high and low bearing rate change.\n"
                "- Car & Taxi: High speed (20–100 km/h), smoother trajectory with low bearing rate change.\n"
                "- Train: High constant speed (60–300 km/h), very low bearing change, and straight-line trajectory.\n"
                "- Airplane: Extremely high speed (300+ km/h) with almost no bearing rate change except at start and end.\n"
                "- Other: Unusual patterns that do not match the above categories.\n\n"

                "Use the following features for more accurate classification:\n"
                "- Speed and its variation over time.\n"
                "- Acceleration and deceleration patterns.\n"
                "- Bearing rate change (sharp turns or consistent direction).\n"
                "- Distance covered in short time intervals.\n"
                "- Start and end locations (e.g., airports, train stations, bus terminals, urban streets) for additional context.\n\n"

                "In your responses, explain the logic behind the prediction based on the available data and trajectory patterns. And only provide on pridiction!"
            )
        }
    ]
        self.max_history = max_history

    def transform_query(self, user_query):
        """
        Uses ChatGPT to transform the user query into a more optimized query for Qdrant.
        
        Args:
            user_query (str): The original user query.
        
        Returns:
            str: A transformed query suitable for generating an embedding.
        """
        print("Transforming user query for optimized Qdrant search...")
        transformation_prompt = (
        f"Transform this query into a free-of-noisy-words concise and specific description of the trajectory-relevant sentence or keywords:\n\n"
        f"User Query: {user_query}\nTransformed Query:"
        )
        response = azure_openai.chat.completions.create(
            model="gpt-4o",  # Replace with your actual deployment name
            messages=[{"role": "system", "content": "You are a query optimization assistant."},
                      {"role": "user", "content": transformation_prompt}]
        )
        
        transformed_query = response.choices[0].message.content.strip()
        print(f"Transformed Query: {transformed_query}")
        return transformed_query

    def query_qdrant(self, user_query, top_k=5, use_embedding=True, metadata_filter=None):
        """
        Query the Qdrant index using either embedding-based search or metadata-based filtering.
        
        Args:
            user_query (str): The original user query.
            top_k (int): The number of top results to retrieve from Qdrant.
            use_embedding (bool): Whether to use embedding-based search. If False, it will use metadata filtering.
            metadata_filter (dict): A filter for querying by metadata (e.g., duration, speed range).
        
        Returns:
            list: A list of trip descriptions from the Qdrant index.
        """
        if use_embedding:
            print("Performing embedding-based search...")
            transformed_query = self.transform_query(user_query)
            query_embedding = generate_embedding(transformed_query)
            
            search_results = qdrant_client.search(
                collection_name=qdrant_collection_name,
                query_vector=query_embedding.tolist(),
                limit=top_k,
                with_payload=True
            )
        
        else:
            print("Performing metadata-based search...")
            if metadata_filter is None:
                raise ValueError("Metadata filter must be provided for metadata-based search.")
            
            search_results = qdrant_client.scroll(
                collection_name=qdrant_collection_name,
                scroll_filter=metadata_filter,  # Use `scroll_filter` instead of `filter`
                limit=top_k,
                with_payload=True
            )
        
        print("Top matches:")
        trip_descriptions = []
        # Ensure we correctly extract the first element if Qdrant returns a tuple
        actual_results = search_results[0] if isinstance(search_results, tuple) else search_results

        for i, result in enumerate(actual_results):  
            print(f"Match {i+1}:")  
            print(result.payload['description'])  
            print("-" * 40)  
            trip_descriptions.append(result.payload['description'])  

        
        return trip_descriptions

    def reset_history(self):
        """Resets the chat history to the initial system message."""
        self.messages = [
            {
                "role": "system",
                "content": (
                    "You are a specialized AI assistant for analyzing and predicting the mode of transportation based on GPS trajectory data. "
                    "Your primary task is to classify the transportation mode (e.g., Walk, Bike, Bus, Car & Taxi, Train, Airplane, Other) by using trajectory features such as speed, acceleration, and bearing rate change."
                )
            }
        ]
        print("Chat history reset.")

    def send_message(self, question, use_metadata=False, metadata_filter=None):
        """
        Send a query to the assistant, which interacts with Qdrant using either embedding-based search or metadata filtering.
        
        Args:
            question (str): The user query.
            use_metadata (bool): If True, use metadata-based search; otherwise, use embedding-based search.
            metadata_filter (dict): The filter to apply if use_metadata is True.
        
        Returns:
            str: The assistant's response.
        """
        reminder_message = {
            "role": "system",
            "content": "Focus on answering the question using GIS-related knowledge and trip description context."
        }
        self.messages.append(reminder_message)
        
        user_message = {
            "role": "user",
            "content": question
        }
        self.messages.append(user_message)
        
        if len(self.messages) > self.max_history:
            self.messages = self.messages[-self.max_history:]
        
        # Query Qdrant to get relevant trip descriptions
        trip_descriptions = self.query_qdrant(
            user_query=question, 
            use_embedding=not use_metadata,  # Switch based on the use_metadata flag
            metadata_filter=metadata_filter
        )
        
        trip_descriptions = [
            desc.replace("\n    - Transport Mode: bike", "") for desc in trip_descriptions
        ]
        print(trip_descriptions)
        if trip_descriptions:
            self.messages.append({
                "role": "system",
                "content": "Here are some relevant trip descriptions from the dataset:\n" + "\n".join(trip_descriptions)
            })
        
        # Call the OpenAI API to respond to the user
        response = azure_openai.chat.completions.create(
            model="gpt-4o",  # Replace with your actual deployment name
            messages=self.messages
        )
        
        assistant_message = {"role": "assistant", "content": response.choices[0].message.content}
        self.messages.append(assistant_message)
        
        return response.choices[0].message.content

# # Example usage
ai_assistant = SpatioAIQueryAssistant()
# response = ai_assistant.send_message("for trajectory data that have date of 2009-05-24 (speed, distance, bearing change, and duration), predict the most likely mode of transportation. Explain your reasoning and provide any alternative possibilities.")
# print("Assistant:", response)


In [174]:
# # Example 1: Embedding-based search (default)
# response = ai_assistant.send_message(
#     "For trajectory data from 2009-09-23, predict the most likely mode of transportation."
# )
# print("Assistant:", response)

# Example 2: Metadata-based search for trips on 2009-09-23
metadata_filter = {
    "must": [
        {"key": "start_datetime", "range": {"gte": "2011-10-28T00:00:00", "lte": "2011-10-28T23:59:59"}}
    ]
}
response = ai_assistant.send_message(
    "Describe trips on 2011-10-28.",
    use_metadata=True,
    metadata_filter=metadata_filter
)
print("Assistant:", response)


Performing metadata-based search...
Top matches:
Match 1:

    Trip Summary:
    - Start: 2011-10-28 01:28:01 at 中关村南路, 科育社区, 中关村街道, 海淀区, 北京市, 100086, 中国
    - End: 2011-10-28 01:37:33 at 新东方大厦, 6, 海淀中街, 中关村核心区, 海淀街道, 海淀区, 北京市, 100080, 中国
    - Duration: 0 days 00:09:32
    - Distance: 2.37 km
    - Average Speed: 16.29 km/h
    - Average Bearing Change: 48.03 degrees
    - Transport Mode: bike
    
----------------------------------------
['\n    Trip Summary:\n    - Start: 2011-10-28 01:28:01 at 中关村南路, 科育社区, 中关村街道, 海淀区, 北京市, 100086, 中国\n    - End: 2011-10-28 01:37:33 at 新东方大厦, 6, 海淀中街, 中关村核心区, 海淀街道, 海淀区, 北京市, 100080, 中国\n    - Duration: 0 days 00:09:32\n    - Distance: 2.37 km\n    - Average Speed: 16.29 km/h\n    - Average Bearing Change: 48.03 degrees\n    ']
Assistant: Based on the provided data, here is a detailed analysis of the trip on 2011-10-28:

1. **Trip Overview**:
   - **Start Time**: 2011-10-28 01:28:01
   - **End Time**: 2011-10-28 01:37:33
   - **Start Location**: 中关村南

In [173]:
ai_assistant.reset_history()

Chat history reset.


In [27]:
def count_points_in_qdrant():
    no_valid_data_count = qdrant_client.count(
        collection_name=qdrant_collection_name,
        count_filter={"must": [{"key": "description", "match": {"value": "No valid data for this trip."}}]}
    )

    valid_data_count = qdrant_client.count(
        collection_name=qdrant_collection_name,
        count_filter={"must_not": [{"key": "description", "match": {"value": "No valid data for this trip."}}]}
    )

    print(f"Number of points with 'No valid data for this trip.': {no_valid_data_count.count}")
    print(f"Number of points with valid data: {valid_data_count.count}")

# Call the function
count_points_in_qdrant()

Number of points with 'No valid data for this trip.': 0
Number of points with valid data: 24
